# COMP309 - a4
### Elliott Rose
### 300540768
## Part 2:

In [11]:
import pandas as pd
import numpy as np
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, roc_auc_score

from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier, AdaBoostClassifier, GradientBoostingClassifier
from sklearn.svm import SVC
from sklearn.neural_network import MLPClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis

In [12]:
column_names = ['age', 'workclass', 'fnlwgt', 'education', 'education-num', 'marital-status', 'occupation', 'relationship', 'race', 'sex', 'capital-gain', 'capital-loss', 'hours-per-week', 'native-country', 'income']
train_data = pd.read_csv('Part 2 - classification/adult.data', header = None)
test_data = pd.read_csv('Part 2 - classification/adult.test', header = None, skiprows = [0]) # removing first row because its useless
train_data.columns = column_names
test_data.columns = column_names

# missing data handling
train_data.replace('?', np.nan)
test_data.replace('?', np.nan)

# dropping the education column
train_data.drop(columns=['education'], inplace=True)
test_data.drop(columns=['education'], inplace=True)

# combining capital-gain and loss
train_data['net-capital'] = train_data['capital-gain'] - train_data['capital-loss']
test_data['net-capital'] = test_data['capital-gain'] - test_data['capital-loss']
train_data.drop(columns=['capital-gain'], inplace=True)
train_data.drop(columns=['capital-loss'], inplace=True)
test_data.drop(columns=['capital-loss'], inplace=True)
test_data.drop(columns=['capital-gain'], inplace=True)

# splitting target feature from the rest
train_incomes = train_data["income"]
test_incomes = test_data["income"]
x_train = train_data.drop(columns = ["income"])
x_test = test_data.drop(columns = ["income"])

# removing . from the end of target feature
for i, string in enumerate(test_incomes):
    string = test_incomes[i]
    test_incomes[i] = string[:-1]

# getting categorical and numeric features
categorical_columns = x_train.select_dtypes(include=['object']).columns.to_list()
numerical_columns = x_train.select_dtypes(include=['number']).columns.to_list()

# encoding some features separately
def isUS(country):
    if(country == " United-States"):
        return True
    else: return False

def overUnder(income):
    if income == " >50K":
        return 1
    else:
        return 0
    
def isMarried(person):
    substring = 'Married'
    if(substring in person):
        return True
    else: return False
    
x_train["native-country"] = x_train["native-country"].map(isUS)
x_test["native-country"] = x_test["native-country"].map(isUS)
x_train["marital-status"] = x_train["marital-status"].map(isMarried)
x_test["marital-status"] = x_test["marital-status"].map(isMarried)
train_incomes = train_incomes.map(overUnder)
test_incomes = test_incomes.map(overUnder)

# encoding categorical features not including native country
train_data_encoded = pd.get_dummies(x_train)
test_data_encoded = pd.get_dummies(x_test)

# scaling the numerical features
scaler = StandardScaler()
train_encoded_scaled = scaler.fit_transform(train_data_encoded[numerical_columns])
test_encoded_scaled = scaler.transform(test_data_encoded[numerical_columns])

C:\Users\ellio\AppData\Local\Temp\ipykernel_13508\2825428647.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test_incomes[i] = string[:-1]
C:\Users\ellio\AppData\Local\Temp\ipykernel_13508\2825428647.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test_incomes[i] = string[:-1]
C:\Users\ellio\AppData\Local\Temp\ipykernel_13508\2825428647.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test_incomes[i] = string[:-1]
C:\User

In [13]:
train_data_encoded.columns

Index(['age', 'fnlwgt', 'education-num', 'marital-status', 'hours-per-week',
       'native-country', 'net-capital', 'workclass_ ?',
       'workclass_ Federal-gov', 'workclass_ Local-gov',
       'workclass_ Never-worked', 'workclass_ Private',
       'workclass_ Self-emp-inc', 'workclass_ Self-emp-not-inc',
       'workclass_ State-gov', 'workclass_ Without-pay', 'occupation_ ?',
       'occupation_ Adm-clerical', 'occupation_ Armed-Forces',
       'occupation_ Craft-repair', 'occupation_ Exec-managerial',
       'occupation_ Farming-fishing', 'occupation_ Handlers-cleaners',
       'occupation_ Machine-op-inspct', 'occupation_ Other-service',
       'occupation_ Priv-house-serv', 'occupation_ Prof-specialty',
       'occupation_ Protective-serv', 'occupation_ Sales',
       'occupation_ Tech-support', 'occupation_ Transport-moving',
       'relationship_ Husband', 'relationship_ Not-in-family',
       'relationship_ Other-relative', 'relationship_ Own-child',
       'relationship_ U

In [14]:
models = [
    LogisticRegression(),
    KNeighborsClassifier(),
    DecisionTreeClassifier(),
    RandomForestClassifier(),
    AdaBoostClassifier(),
    GradientBoostingClassifier(),
    SVC(),
    MLPClassifier(),
    GaussianNB(),
    LinearDiscriminantAnalysis()
]

model_scores = {
    'Model' : [],
    'Accuracy' : [],
    'Precision' : [],
    'Recall' : [],
    'F1-score' : [],
    'AUC' : []
}

for model in models:
    model.fit(train_encoded_scaled, train_incomes)
    pred = model.predict(test_encoded_scaled)
    accuracy = accuracy_score(test_incomes, pred)
    precision = precision_score(test_incomes, pred)
    recall = recall_score(test_incomes, pred)
    f1 = f1_score(test_incomes, pred)
    auc = roc_auc_score(test_incomes, pred)
    model_scores['Model'].append(str(model))
    model_scores['Accuracy'].append("{:.2f}".format(accuracy))
    model_scores['Precision'].append("{:.2f}".format(precision))
    model_scores['Recall'].append("{:.2f}".format(recall))
    model_scores['F1-score'].append("{:.2f}".format(f1))
    model_scores['AUC'].append("{:.2f}".format(auc))

model_scores_df = pd.DataFrame(model_scores)
model_scores_df.to_csv('part2.csv', index=False)
model_scores_df

c:\Users\ellio\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\ensemble\_weight_boosting.py:527: FutureWarning: The SAMME.R algorithm (the default) is deprecated and will be removed in 1.6. Use the SAMME algorithm to circumvent this warning.
  warnings.warn(


Model Accuracy Precision Recall F1-score   AUC
0          LogisticRegression()     0.81      0.67   0.36     0.47  0.65
1        KNeighborsClassifier()     0.80      0.60   0.44     0.51  0.67
2      DecisionTreeClassifier()     0.77      0.51   0.53     0.52  0.69
3      RandomForestClassifier()     0.81      0.62   0.51     0.56  0.71
4          AdaBoostClassifier()     0.84      0.79   0.41     0.54  0.69
5  GradientBoostingClassifier()     0.84      0.78   0.45     0.57  0.71
6                         SVC()     0.82      0.77   0.35     0.48  0.66
7               MLPClassifier()     0.82      0.71   0.43     0.54  0.69
8                  GaussianNB()     0.80      0.75   0.23     0.35  0.60
9  LinearDiscriminantAnalysis()     0.80      0.66   0.32     0.43  0.63